In [1]:
import pandas as pd
from pandas.api.types import CategoricalDtype
import numpy as np
import os
import sys
import time
import pickle
import altair as alt
from Bio import SeqIO
import multiprocessing

#my HHsuite module in ~/scripts
import parseHHsuite as HH

#----- NOTEBOOK CONFIG ------

#disable altair max rows
alt.data_transformers.disable_max_rows()
#get default altair style
%run ~/scripts/altair_style_config_default.py

pd.set_option('display.expand_frame_repr', False)
pd.set_option('display.max_colwidth', 300)

#enable output scrolling rather than wrapping
from IPython.display import display, HTML
display(HTML("<style>div.output_area pre {white-space: pre;}</style>"))



root = '/home/tobiassonva/data/eukgen/'
%cd {root}


/vf/users/tobiassonva/data/eukgen


In [ ]:
#print mmeory usage of python objects
import sys

# These are the usual ipython objects, including this one you are creating
ipython_vars = ['In', 'Out', 'exit', 'quit', 'get_ipython', 'ipython_vars']

# Get a sorted list of the objects and their sizes
a = sorted([(x, sys.getsizeof(globals().get(x))/(1024**3)) for x in dir() if not x.startswith('_') and x not in sys.modules and x not in ipython_vars], key=lambda x: x[1], reverse=True)
print(*[size for size in a], sep='\n')
sum([size[1] for size in a])


In [ ]:
#small helper for pkl parsing
def load_pkl(pkl_file):
    import parseHHsuite as HH
    with open(pkl_file, 'rb') as infile:
        item = pickle.load(infile)
    return item

def dump_pkl(item, pkl_file):
    with open(pkl_file, 'wb') as outfile:
        pickle.dump(item, outfile)
    print(f'Pickled item as {pkl_file}')

#pandas helper function to reset_index inplace
def reindex(df, column):
    df.sort_values(by=column, inplace=True)
    df.set_index(keys=[column], drop=True,inplace=True)
    

    
#take a list of strings and return counts of words separated by spaces 
#ignores anything contained in regex blacklist expression
def calculate_label_counts(labels, blacklist='(protein)'):
    words = [label.split() for label in labels]
    words = [item for sublist in words for item in sublist]
    
    #remove common phrases from filter
    words = pd.Series(words)[~(pd.Series(words).str.contains(blacklist, regex=True))]

    word_counts = words.value_counts()
    
    return word_counts



#basic try to ammend the cropping of profile headers employed by hhsuite, capped at 138 or 142 chars??
#requires searchDF from parse_HHsuite or equivalent Query, Target dataframe
#requires global reference header mapping for both query and targets containing acc and header info as index

def create_hhsuite_header_mapping(searchDF, global_header_mapping):

    accs = []

    #append Target and Query columns 
    entries = pd.concat([searchDF.Query, searchDF.Target]).unique()

    #iterate over entries and try to find a accession
    for hit in entries:
        #initial attempt by direct matching
        try:
            hit_acc = global_header_mapping.loc[hit].acc
        
        #for cropped entriestry to slice acc from first space separated element
        #then refer to the global mapping for header
        except KeyError:
            print('cannot find hit for', hit)
            print('trying via acc')
            hit_acc = hit.split()[0]
            new_header = global_header_mapping[global_header_mapping.acc == hit_acc].index[0]
            #print(new_header)
            #print('new acc is', hit_acc) 
        accs.append(hit_acc)

    #format and return DF
    hhsuite_header_mapping = pd.DataFrame({'acc': accs, 'header':entries})

    hhsuite_header_mapping.sort_values(by='header', inplace=True)
    hhsuite_header_mapping.set_index(keys=['header'], drop=True,inplace=True)
    
    return hhsuite_header_mapping


#alignment "viewer style" plot for HHSuite alignments
#takes input as pandas Series containing the 6 series of an HHSuite alignment
#returns the processed dataframe and the altari chart object
#
#Query_sequence     RRRILGPMSSMMMAMAFLSTYPPEFIKRGLEGLRPDGRRPNELRPI...
#Query_consensus    ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~R~DGR~~delRpI...
#Matches            |+..++.-.||||.+.--   +++-+  ..+++|+|||.+||+|||...
#Target_consensus   ~~~~~~~~~~~~~~~~~~---~~~~~--~~~~~R~dGR~~deLRpv...
#Target_sequence    LSHWLGASGSMMMMMTMQ---MPKLI--DENMMRPDGRAPDELRPV...
#Confidence         455667677777765432   22333  249999999999999999...

def plot_alignment(alignmentDF, query_name, target_name):

    alignmentDF = pd.DataFrame({i:list(alignmentDF[i]) for i in alignmentDF.index})
    alignmentDF['seqn'] = alignmentDF.index
    alignmentDF['opacity'] = [np.tanh(int(i)/4) if i != ' ' else 0 for i in alignmentDF.Confidence]
    alignmentDF_melt = alignmentDF.melt(id_vars=['seqn', 'opacity'], value_vars=alignmentDF.columns[:-1], var_name='series', value_name='token')



    #style configuration
    token_color_dict = {'-': 'white','~': 'white','|': 'white', '+': 'white','.': 'white',' ': 'white',
                    '1': 'white', '2': 'white', '3': 'white', '4': 'white', '5': 'white', '6': 'white', '7': 'white', '8': 'white', '9': 'white',
                    'R': '#6276ba', 'K': '#7297c1', 'H': '#7297c1', 'D': '#b25652', 'E': '#b25652', 'S': '#b5b65e', 'T': '#94ae57', 'N': '#72a551', 'Q': '#72a551', 'C': '#cca389', 'G': '#c4ced4', 'P': '#95b5c7', 'A': '#bfa764', 'V': '#b5b65e', 'I': '#94ae57', 'L': '#72a551', 'M': '#cca389', 'F': '#d8c7be', 'Y': '#c4ced4', 'W': '#6276ba',
                    'r': '#c7cee6', 'k': '#b5c9df', 'h': '#b5c9df', 'd': '#e3c2c0', 'e': '#e3c2c0', 's': '#e6e6c6', 't': '#c8d6a8', 'n': '#bed7ae', 'q': '#bed7ae', 'c': '#ead6c9', 'g': '#eef1f3', 'p': '#d1e0e8', 'a': '#e0d6b5', 'v': '#e6e6c6', 'i': '#c8d6a8', 'l': '#bed7ae', 'm': '#dfc7b6', 'f': '#eee7e3', 'y': '#e0e6e8', 'w': '#b5bfde'}

    seq_len = alignmentDF_melt.seqn.max()
    series_number = len(alignmentDF.columns)
    scale = 12

    title = ['Query:    \t'+query_name, 'Target:   \t'+target_name]

    token_names = list(token_color_dict.keys())
    token_colors = list(token_color_dict.values())
    sort_order = ['Confidence', 'Query_sequence', 'Query_consensus', 'Matches', 'Target_consensus', 'Target_sequence']

    #base chart 
    base = alt.Chart(alignmentDF_melt, title=title).encode(
        alt.X('seqn:O', axis=alt.Axis(title=None, values=list(range(0,seq_len,5)), grid=False)),
        alt.Y('series:O', sort=sort_order, axis=alt.Axis(grid=False, title=None, labelFontSize=scale)),
        alt.Opacity('opacity', legend=None),
    ).properties(width=seq_len*scale*1.4, height=series_number*scale*1.4)

    #residue labels
    text = base.mark_text(color ='black', align='center', fontSize=scale).encode(
        alt.Text('token')
    )

    #colored boxes
    box = base.mark_rect().encode(
        alt.Color('token', scale=alt.Scale(domain=token_names, range=token_colors),
                 legend=alt.Legend(direction='horizontal', columns=4, orient='left', title=None, labelFontSize=scale,
                                   values=['R', 'K', 'H', 'D', 'E', 'S', 'T', 'N', 'Q', 'C', 'G', 'P', 'A', 'V', 'I', 'L', 'M', 'F', 'Y', 'W']))
    )

    chart = alt.layer(box, text).configure_title(fontSize=scale*1.5)

    return alignmentDF, chart


#calculate cumulative sum and distribution for pd.Series
#takes pd.Series as input and returns a parsed DF and altair chart object 
def plot_cumsum_counts(series, title='Chart', x_label='value', y_label='count', 
                       x_min=0, y_min=0, x_max=None, y_max=None,
                       x_scale_type='log', y_scale_type='log', decimals=2):
    
    #format DF for data handling, filter 0 values for plot 
    #round to reduce float data display jaggedness
    series = series[series!=0].round(decimals)
    
    #format distribution dataframe
    countDF = pd.DataFrame(series.value_counts())
    countDF.columns = ['amount']
    countDF.sort_index(inplace=True)
    countDF['cumsum'] = countDF['amount'].cumsum()
    countDF['frac_cumsum'] = countDF['cumsum']/countDF['cumsum'].max()
    countDF.reset_index(inplace=True)
    
    #rename columns for plotting
    countDF.columns = [x_label,y_label,'cumsum','frac_cumsum']

    #format axis domains
    x_range = [x_min, series.max()]
    y_range = [y_min, countDF[y_label].max()]
    
    if x_max:
        x_range = [x_min, x_max]
    
    if y_max:
        y_range = [y_min, y_max]
        
    #plot cumulative distribution
    chart_cumsum = alt.Chart(countDF, title=title).mark_line(color=colorlib['twilight_shifted_r_perm'][2],
                                              strokeWidth=3).encode(
        x=alt.X(x_label, title=x_label, scale=alt.Scale(type=x_scale_type)),
        y=alt.Y('frac_cumsum', title='Cumulative Fraction', scale=alt.Scale(domain=[0,1]), axis=alt.Axis(labelAlign='left')),
        tooltip=alt.Tooltip([x_label, y_label, 'frac_cumsum'])
    )
    
    #plot value distribution
    chart_bar = alt.Chart(countDF).mark_area(interpolate='step-after', 
                                            fillOpacity=0.2, line=True).encode(
        x=alt.X(x_label+':Q', scale=alt.Scale(domain=x_range, type=x_scale_type)),
        y=alt.Y(y_label, scale=alt.Scale(domain=y_range, type=y_scale_type)),
        tooltip=alt.Tooltip([x_label, y_label, 'frac_cumsum'])
    )

    #merge and configure
    merge = alt.layer(chart_bar, chart_cumsum).resolve_scale(y='independent').interactive()

    return countDF, merge




#parse HHSuite outfut fromm ffdata into pkl files 
def parse_and_write(file):
    print(file)
    new_data = HH.load_HHBlitsData(file)
    new_data.write_pkl(file+'.pkl')
    #new_data.write_data_tsv(file+'.tsv')


def parse_filter_write(file):
    thread = multiprocessing.current_process().pid
    print(f'{thread} reading {file}\n')
    new_data = HH.load_HHBlitsData(file)
    new_data.write_pkl(file+'.pkl')
    print(f'{thread} parsing\n')

    for key, query in new_data.data.items():
        query.add_self_hit()
        query.filter_numeric(field='Pairwise_cov', min=20, replace=True, keep_self=True)
        query.filter_numeric(field='Prob', min=50, replace=True, keep_self=True)
    
    print(f'{thread} writing\n')
    new_data.write_pkl(file+'.pkl_filtered')   

In [ ]:
#parallel read and filter all data in files, save to pkl

search_root='search/euk-prok/search/'
files = [search_root+file for file in os.listdir(search_root) if file.endswith('ffdata')]

with multiprocessing.Pool(processes=16) as pool:
    pool.map(parse_filter_write, files)
    

    
#open all parsed pkl files in folder and merge into one object

all_data = HH.HHblitsData()
search_root='search/euk-prok/pkl/'
pkl_filtered_files = [file for file in os.listdir(search_root) if file.endswith('pkl')]

for i, file in enumerate(pkl_filtered_files):
    print(i,file)
    new_data = HH.HHblitsData()
    new_data.load_from_pkl(search_root+file)
    all_data.add_entries(new_data.data)

    
#all_data.write_pkl(search_root+'merged_filtered_self-match.pkl')
#all_data.write_data_tsv(search_root+'merged_filtered_self-match.csv')

In [ ]:
## load data from /analysis/core_data

#clustering data

print('Loading clustering data')
euk_clust = load_pkl(root+'analysis/core_data/euk72_filtered-prof-search-clust.pkl')['members']
prok_clust = load_pkl(root+'analysis/core_data/prok2111_filtered-prof-search-clust.pkl')['members']

reindex(euk_clust, 'cluster_acc')
reindex(prok_clust, 'cluster_acc')

# header mapping

print('Loading header mapping')
euk_header = load_pkl(root+'analysis/core_data/euk72_header_mapping.pkl')
prok_header = load_pkl(root+'analysis/core_data/prok2111_header_mapping.pkl')

reindex(euk_header, 'header')
reindex(prok_header, 'header')

#hhsuite profile header mapping as hhsuite crops header info
hhsuite_header = load_pkl(root+'analysis/core_data/hhsuite_header_mapping.pkl')

#cluster taxonomic filter info
print('Loading taxonomy info')
euk_tax = load_pkl('euk72/euk72_protein_taxonomy.pkl')

#full prok tax
#prok_tax = load_pkl('prok2111/prok2111_protein_taxonomy.pkl')

#lighter parsed version
prok_tax = load_pkl('analysis/core_data/prok2111_protein_taxonomy_trimmed.pkl')

#search data
print('Loading search data')
#full searchDF
#searchDF = load_pkl(root+'analysis/core_data/merged_filtered_cov20_self-match_tsv.pkl')

#parsed acc viersion without alignment, self hits and indexed in query
searchDF = load_pkl('analysis/core_data/merged_filtered_cov20_self-match_tsv_edited_no_aln.pkl')

search_queries = load_pkl(root+'analysis/core_data/merged_filtered_cov20_self-match_tsv.query.pkl')

In [ ]:
#given a series of query accessions, retreive all proteins from prokaryotic hits and return their phylogenetic distribution count
#designed for multiprocess Pool and checkpointing to .pkl files
#not very portable 

def get_hit_tax_dist(queries):
    stime = time.time()
    querynr = len(queries)
    
    thread = multiprocessing.current_process().pid
    print(f'{thread}: started\n')
    
    print(f'{thread}: processing {querynr} queries\n')
    
    #load data from files 
    print(f'{thread}: loading search\n')
    searchDF = load_pkl(root+'analysis/core_data/merged_filtered_cov20_self-match_tsv_edited_no_aln.pkl')
    
    print(f'{thread}: loading clust\n')
    prok_clust = load_pkl(root+'analysis/core_data/prok2111_filtered-prof-search-clust.pkl')['members']
    reindex(prok_clust, 'cluster_acc')

    print(f'{thread}: loading tax\n')
    prok_tax = load_pkl('analysis/core_data/prok2111_protein_taxonomy_trimmed.pkl')

    #process only the given slice
    searchDF = searchDF[(searchDF.Query.isin(queries)) &
                         (searchDF.Query != searchDF.Target) &
                         (searchDF.Pairwise_cov > 0.5)]

    #set index for faster iterating over queries
    searchDF.sort_values(by='Query', inplace=True)
    searchDF.set_index(keys=['Query'], drop=True, inplace=True)

    #iterate and pool taxa distributions
    taxa = {}
    n = 0
    printn = 50
    checkn = 1000

    for query in queries:
        
        if n%printn == 0:
            print(f'{thread}: calculating {query} \t{n}|{querynr} \tT+{round(time.time()-stime)} seconds\n')
        
        #find all target profile hits
        profiles = pd.Series(searchDF.loc[query, 'Target'])

        #find all proteins in target profile hits
        proteins = pd.Series(prok_clust.loc[profiles,'acc'])

        #find all taxonomic information from proteins in taget profile hits
        query_taxa = prok_tax.loc[proteins, 'class'].value_counts()

        #add to dict
        taxa[query] = query_taxa
        
        #itermediate save
        if n != 0 and n%checkn == 0:
            print(f'{thread}: saved checkpoint {n/checkn}')
            dump_pkl(taxa, f'analysis/core_data/tax/{thread}_checkpoint_{int(n/checkn)}_tax.pkl')
            taxa = {}
            
        n+=1
        
    dump_pkl(taxa, f'analysis/core_data/tax/{thread}_tax.pkl')
    return taxa





#launch parallel execution
queries = searchDF[(searchDF.Query != searchDF.Target)
                    & (searchDF.Pairwise_cov > 0.5)].Query.unique()

splits = np.array_split(queries, 16)
with multiprocessing.Pool(processes=16) as pool:
    pool.map(get_hit_tax_dist, splits)
    
    
#load data from savepoints into one dictionary
tax_data = {}
for file in os.listdir('analysis/core_data/tax/'):
    print('analysis/core_data/tax/'+file)
    data = load_pkl('analysis/core_data/tax/'+file)
    tax_data = tax_data.copy()
    tax_data.update(data)
    
#merge dict series into one dataframe
query_tax = pd.DataFrame()
for query, data in tax_data.items():
    print(query)

    data.name = query
    
    temp_tax = pd.DataFrame(data).transpose()
    query_tax = pd.concat([query_tax, temp_tax])

#save processed dataframe
dump_pkl(query_tax, 'analysis/core_data/hit_distribution_cov50.pkl')




#calculate query statistics tables
#load raw hit counts
query_tax = load_pkl('analysis/core_data/hit_distribution_cov50.pkl')

#normalize to relative total hits
query_tax_rel = query_tax.div(query_tax.sum(axis=1), axis=0)
#calculate percentile ranks for relative observations skipping 0 observations
query_tax_rel_percentile = query_tax_rel.apply(lambda df: df[df!=0].rank(method='max', pct=True), axis=0).fillna(0)

#multiply by individual hits to get weights
query_tax_weight = pd.DataFrame(query_tax.values*query_tax_rel.values, columns=query_tax.columns, index=query_tax.index)
#calculate percentile rank of observation of weight
query_tax_weight_percentile = query_tax_weight.apply(lambda df: df.rank(method='max', pct=True), axis=0)


#write proteins from query clusters which have top 10% relative hits in 
#respective taxon to file

prominent_taxon_proteins = {}
for taxon in query_tax.columns:
    prominent_queries = query_tax_rel_percentile[(query_tax_rel_percentile[taxon].between(0.85, 0.90))].index
    prominent_proteins = euk_clust.loc[prominent_queries, 'acc'].values

    homo_tax = euk_tax[euk_tax['class'] == 'Mammalia']
    prominent_homo_proteins = homo_tax[homo_tax.index.isin(prominent_proteins)].index
    outdata = euk_header[euk_header.acc.isin(prominent_homo_proteins)]
    print(taxon, outdata.shape[0])
    outdata.reset_index(inplace=True)
    
    outdata['header'].to_csv(f'analysis/core_data/significant/{taxon.replace(" ", "_")}.tsv', sep='\t', index=None, header=None)
    


In [ ]:
#example quesries for testing
euk_queries_test1 = ['OLP83888.1', 'SPQ97222.1', 'XP_009012109.1', 'XP_001461706.1',
       'OLP92683.1', 'XP_002965802.1', 'XP_024530808.1', 'OLP86390.1',
       'KAA0160735.1', 'XP_002681799.1', 'XP_002113075.1', 'OLQ13277.1',
       'XP_001469768.1', 'XP_008902708.1', 'XP_002682078.1', 'XP_024309865.1',
       'OLP87304.1', 'XP_004365904.1', 'XP_012899378.1', 'XP_032224311.1',
       'XP_032223284.1', 'XP_001707828.1', 'XP_005536084.1', 'XP_018187362.1',
       'XP_645838.1', 'PXF40497.1', 'XP_005847475.1', 'KAA0160637.1',
       'XP_013754706.1', 'XP_008905306.1']

euk_queries_test2 = ['CBN77353.1', 'CEL94470.1', 'CEL98020.1', 'CEM00912.1',
       'CEM13793.1', 'CEO94447.1', 'CEP02189.1', 'CEP02404.1',
       'EPZ31333.1', 'GBG32138.1', 'GBG34166.1', 'GBG34636.1',
       'GBG88810.1', 'KAA0151157.1', 'KAA0167757.1', 'KAA6364588.1',
       'KAA6383781.1', 'NP_001022034.1', 'NP_001105121.2',
       'NP_001170744.1', 'NP_001189295.1', 'NP_001242666.1',
       'NP_001259573.1', 'NP_001261837.1', 'NP_001294564.1',
       'NP_001307934.1', 'NP_001328712.1', 'NP_012528.1', 'NP_050092.1',
       'NP_051148.1', 'NP_189541.1', 'NP_197350.1', 'NP_498455.2',
       'NP_505960.3', 'NP_588329.1', 'NP_595422.1', 'NP_609709.1',
       'NP_611238.2', 'NP_649295.1', 'OAD00700.1', 'OAD03858.1',
       'OAD05886.1', 'OAE33051.1', 'OLP78629.1', 'OLQ06972.1',
       'OLQ08228.1', 'OLQ08510.1', 'OLQ11720.1', 'OLQ12045.1',
       'OLQ14344.1']

euk_queries_test3 = ['XP_008911403.1', 'XP_011408184.1', 'XP_002681038.1', 'XP_002673113.1',
                     'OAD09041.1', 'XP_001634466.1', 'XP_005765180.1', 'XP_011407364.1', 
                     'XP_005789988.1', 'KAA6344160.1', 'KAA6409619.1', 'XP_002287408.1',
                     'OAE21175.1', 'RKP17192.1', 'XP_013760427.1', 'KAA0163767.1',
                     'XP_002119908.1', 'XP_009692086.1']

#queries in superkingdoms with between 20, 50 mmebers hitting less than 20 prokaryotic profiles
#and the representative seuqence is from a fish, insect or mammal
euk_queries_test4 = ['NP_001002332.1', 'NP_001240313.1',
       'NP_001259573.1', 'NP_001260847.1', 
       'NP_001278869.1', 'NP_001307724.1', 'NP_001307934.1', 'NP_001334755.1',
       'NP_001356620.1', 'NP_115888.1', 
       'NP_610753.1', 'NP_611238.2', 'NP_956312.1',
       'NP_998197.1', 'NP_998403.1', 'XP_005256905.1',  'XP_017206845.1', 'XP_021326060.1', 'XP_021336265.1']

#queries in superkingdoms with between 20, 50 mmebers hitting less than 20 prokaryotic profiles
#and there are between 200 and 2000 prokaryotic hits 
euk_queries_test5 = ['AGK83073.1', 'CBN73833.1', 'CBN79086.1', 'CEM35385.1', 'CEO94447.1', 'CEP00213.1', 'CEP03651.1', 'EPZ30938.1', 'EPZ31301.1', 'GBG60132.1', 
'GBG70565.1', 'GBG80562.1', 'GBG83744.1', 'KAA0165271.1', 'KAA0172078.1', 'KAA6408708.1', 'NP_001002332.1', 'NP_001259573.1', 'NP_001294564.1',
 'NP_001307724.1', 'NP_001328712.1', 'NP_001334755.1', 'NP_001356620.1', 'NP_011081.1', 'NP_050092.1', 'NP_594946.1', 'NP_610753.1', 'NP_848958.1',
  'NP_849074.1', 'NP_956312.1', 'NP_998197.1', 'OAD04802.1', 'OAD06369.1', 'OAE33370.1', 'OLP84660.1', 'OLQ06972.1', 'OLQ08228.1', 'OLQ14344.1',
   'OSX69435.1', 'OSX71470.1', 'OSX72678.1', 'OSX75094.1', 'OSX77054.1', 'PTQ50428.1', 'PXF41822.1', 'PXF45288.1', 'RKP17849.1', 'RKP18091.1', 
   'RKP20265.1', 'RWR93989.1', 'RWR97906.1', 'RWR98344.1', 'SLM34047.1', 'SLM40311.1', 'SLM40671.1', 'SPQ96285.1', 'SPQ98172.1']


print('Done')

#calcualtion of profiles to be included in MSA evaluation
euk_lca = load_pkl('analysis/core_data/euk72_filtered-prof-search-clust.lca.pkl')
euk_lca_superkingdom = euk_lca[euk_lca.lca.isin(['superkingdom'])].index.unique().values

searchDF_filtered = searchDF[(searchDF.index.isin(euk_lca_superkingdom)) &
                            (searchDF.Pairwise_cov > 0.5) &
                            (searchDF.Prob > 50)]


queries_filtered = searchDF_filtered.index.unique().values


#extended set for full miscrocosm evalution testing
wider_set = searchDF_filtered[(euk_clust.index.value_counts().between(20,1000)) & 
                  (searchDF.index.value_counts().between(2,500))]
wider_set_queries = wider_set.sample(1000).index.unique()[0:200].values

In [ ]:
def structure_microcosm(queries, query_hits, query_clusters, target_clusters, root):    
    root_query = root+query+'/'
    os.mkdir(root_query)

    print(f'Q:{query}')
    query_members = query_clusters.loc[query, 'acc']
    hits = query_hits.loc[query]
    members = target_clusters.loc[hits]

    #write quesry accessions to .acc
    with open(root_query+f'{query}.acc', 'w') as outfile:
        outfile.write(pd.DataFrame(query_members).to_csv(sep='\t', header=None, index=None))

    with open(root_query+f'{query}.targets', 'w') as outfile:
        outfile.write(pd.DataFrame(members).to_csv(sep='\t', header=None))
            

In [ ]:

#describe search results

print('Load data')
#load parse_HHSuite data from pkl 
search_data = HH.HHblitsData()
search_data.load_from_pkl(root+'search/euk-prok/merged_filtered_cov20_self-match.pkl')

#search block csv
search_csv = pd.read_csv(root+'search/euk-prok/merged_filtered_cov20_self-match.csv', sep='\t')
#query block csv
search_queries_csv = pd.read_csv(root+'search/euk-prok/merged_filtered_cov20_self-match.queries.csv', sep='\t', index_col='Query')

#remove self hits
search_nonself_csv = search_csv[(search_csv.Query != search_csv.Target)]

#total hits
print(f'Total hits = {search_nonself_csv .shape[0]}\n')

#identities
probs = search_nonself_csv.Prob.describe()
print('Probability breakdown\n', probs,'\n')

#probabilities
ident = search_nonself_csv.Identities.describe()
print('Identity breakdown\n', ident,'\n')


#calculate number of hits per query and number of queries per hit
print('calculating hit statistics\n')
hits = []
for query in search_data.query_names[0:100000]:
    query_data = pd.DataFrame(search_data.data[query].hit_dict)
    hits.append(query_data[query_data.Target != query].shape[0])
    
inverse_hits = search_nonself_csv.Target.value_counts()

print('Most frequent inverse hits\n')
print(inverse_hits[0:20], '\n')

print('most common words among inverse hits\n')
print(calculate_label_counts(inverse_hits[inverse_hits>100].index)[0:20], '\n')

#plot hit distributions
plot_cumsum_counts(pd.Series(inverse_hits.values)) &  plot_cumsum_counts(pd.Series(hits))

In [ ]:
#plot distribution of probabilities against identities

subset = search_data[search_data.Query != search_data.Target].sample(100000)

chart = alt.Chart(subset).mark_rect().encode(
    x=alt.X('Prob:Q', bin=alt.Bin(extent=[0,100], step=1), axis=alt.Axis(grid=False)),
    y=alt.Y('Identities:Q', bin=alt.Bin(extent=[0,100], step=1), axis=alt.Axis(grid=False)),
    color=alt.Color('count()', scale=alt.Scale(scheme='bluepurple', domain=[-1,200]))

).properties(width=800, height=450)


#precomputed histogram for faster render
#doesn't work properly

xvalue='Prob'
yvalue='Similarity'

xbins = 100
ybins = 100
xrange = [subset[xvalue].min(), subset[xvalue].max()]
yrange = [subset[yvalue].min(), subset[yvalue].max()]

hist_data = np.histogram2d(subset[xvalue], subset[yvalue], 
                           bins=(np.linspace(xrange[0], xrange[1], xbins).round(2), 
                                 np.linspace(yrange[0], yrange[1], ybins).round(2)), density=True)
x = []
y = []
v = []
for i, m in enumerate(hist_data[1][:-1]):
    for j, n in enumerate(hist_data[2][:-1]):
        x.append(m)
        y.append(n)
        v.append(hist_data[0][i][j])
        
hist_data_plot = pd.DataFrame({'xbins': x, 'ybins': y, 'density': v})


alt.Chart(hist_data_plot).mark_rect().encode(
    x=alt.X('xbins:O', axis=alt.Axis(grid=False)),
    y=alt.Y('ybins:O', axis=alt.Axis(grid=False)),
    color = alt.Color('density',  scale=alt.Scale(scheme='bluepurple', domain=[min(v)*5, max(v)/10]))
).properties(width=800, height=450)

------ REFORMATTING FOR CLUSTERING --------

In [ ]:
#dirty check for label consistency of queries and blasttab formatting for mmseqs

root = 'clust/euk72-profiles/profile-profile-hhsearch/'
#header = ['Query','Target','Prob','E-value','P-value','Score','SS','Cols','Identities','Similarity','Sum_probs','Query-HMM-start','Query-HMM-end','Template-HMM-start','Template-HMM-end','Template_columns','Template_Neff']
data = pd.read_csv(root+'merged_data_filtered_c80.tsv', sep = '\t')


In [ ]:
lookup = '/data/tobiassonva/data/eukgen/euk72/euk72.lookup'
lookup = pd.read_csv(lookup, sep='\t', header=None, index_col=1, names=['name', 'index', 'none'])

In [ ]:
#split the labels to get accessions
parse_query = [entry.split()[0] for entry in data.Query]
parse_target = [entry.split()[0] for entry in data.Target]


#find label discrepancies
queries = parse_query
entries = lookup.index

clusters = '/data/tobiassonva/data/eukgen/clust/euk72-profiles/euk72_filtered-casc-clust-6-merged.tsv'
clusters = pd.read_csv(clusters, sep ='\t', header=None, names=['clust', 'mem'])['clust']

a = set(queries).difference(set(clusters))
b = set(clusters).difference(set(queries))

print(a)
print(b)

In [ ]:
#inconsistent labels from mmseqs internal parsing
query = pd.Series(parse_query)

query.replace('pir||A44923', 'A44923',inplace=True)
query.replace('prf||1111187A', '1111187A', inplace=True)
query.replace('prf||1111187C', '1111187C', inplace=True)

target = pd.Series(parse_target)

target.replace('pir||A44923', 'A44923',inplace=True)
target.replace('prf||1111187A', '1111187A', inplace=True)
target.replace('prf||1111187C', '1111187C', inplace=True)

In [ ]:
query_index = [lookup.loc[entry, 'name'] for entry in query]
target_index = [lookup.loc[entry, 'name'] for entry in target]

In [ ]:
query = pd.Series(parse_query)
query_index = [lookup.loc[entry, 'name'] for entry in query]
print('target')
target = pd.Series(parse_target)
target_index = [lookup.loc[entry, 'name'] for entry in target]

In [ ]:
data.Query = query_index
data.Target = target_index
data_queries = data.Query.unique()
data_filtered = data[data.Target.isin(data_queries)]

In [ ]:
#format blasttab format mode 8 for mmseqs tsv2result
blasttab_m8 = pd.DataFrame({'Query': data_filtered.Query, 'Target':data_filtered.Target})

add_columns = ['Identities', 'Template_columns',  'Query-HMM-start','Query-HMM-end','Template-HMM-start','Template-HMM-end','E-value', 'Score']
order = ['Query', 'Target', 'Identities', 'Template_columns', 'Mismatch', 'Gap_open', 'Query-HMM-start','Query-HMM-end','Template-HMM-start','Template-HMM-end','E-value', 'Score']


blasttab_m8[add_columns] = data_filtered[add_columns]
blasttab_m8['Mismatch'] = [0 for _ in blasttab_m8.index]
blasttab_m8['Gap_open'] = [0 for _ in blasttab_m8.index]

blasttab_m8

------ Microcosm formatting --------

In [8]:
from core_functions.hhsuite_functions import merge_hhsuite_search_results

search = 'processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/'
basename = 'processing/search/euk72_ep_vs_prok2111_as_NEW/euk72_ep_vs_prok2111_as_cov80_prob80'

merge_hhsuite_search_results(search_root=search,
    output_basename=basename,
    write_tsv=True,
    filter_cov=0.8,
    filter_prob=80)

Merging all files from processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/ to processing/search/euk72_ep_vs_prok2111_as_NEW/euk72_ep_vs_prok2111_as_cov80_prob80
Parsing file #0: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_0_vs_prok2111_as.ffdata
Parsing file #1: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_100_vs_prok2111_as.ffdata
Parsing file #2: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_101_vs_prok2111_as.ffdata
Parsing file #3: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_102_vs_prok2111_as.ffdata
Parsing file #4: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_103_vs_prok2111_as.ffdata
Parsing file #5: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_104_vs_prok2111_as.ffdata
Parsing file #6: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_105_vs_prok2111_as.ffdata
Parsing file #7: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_106_vs_prok2111_

Parsing file #76: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_169_vs_prok2111_as.ffdata
Parsing file #77: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_16_vs_prok2111_as.ffdata
Parsing file #78: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_170_vs_prok2111_as.ffdata
Parsing file #79: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_171_vs_prok2111_as.ffdata
Parsing file #80: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_172_vs_prok2111_as.ffdata
Parsing file #81: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_173_vs_prok2111_as.ffdata
Parsing file #82: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_174_vs_prok2111_as.ffdata
Parsing file #83: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_175_vs_prok2111_as.ffdata
Parsing file #84: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_176_vs_prok2111_as.ffdata
Parsing file #85: processing/search/eu

Parsing file #153: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_238_vs_prok2111_as.ffdata
Parsing file #154: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_239_vs_prok2111_as.ffdata
Parsing file #155: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_23_vs_prok2111_as.ffdata
Parsing file #156: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_240_vs_prok2111_as.ffdata
Parsing file #157: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_241_vs_prok2111_as.ffdata
Parsing file #158: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_242_vs_prok2111_as.ffdata
Parsing file #159: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_243_vs_prok2111_as.ffdata
Parsing file #160: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_244_vs_prok2111_as.ffdata
Parsing file #161: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_245_vs_prok2111_as.ffdata
Parsing file #162: processing

Parsing file #229: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_306_vs_prok2111_as.ffdata
Parsing file #230: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_307_vs_prok2111_as.ffdata
Parsing file #231: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_308_vs_prok2111_as.ffdata
Parsing file #232: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_309_vs_prok2111_as.ffdata
Parsing file #233: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_30_vs_prok2111_as.ffdata
Parsing file #234: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_310_vs_prok2111_as.ffdata
Parsing file #235: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_311_vs_prok2111_as.ffdata
Parsing file #236: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_312_vs_prok2111_as.ffdata
Parsing file #237: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_313_vs_prok2111_as.ffdata
Parsing file #238: processing

Parsing file #305: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_375_vs_prok2111_as.ffdata
Parsing file #306: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_376_vs_prok2111_as.ffdata
Parsing file #307: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_377_vs_prok2111_as.ffdata
Parsing file #308: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_378_vs_prok2111_as.ffdata
Parsing file #309: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_379_vs_prok2111_as.ffdata
Parsing file #310: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_37_vs_prok2111_as.ffdata
Parsing file #311: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_380_vs_prok2111_as.ffdata
Parsing file #312: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_381_vs_prok2111_as.ffdata
Parsing file #313: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_382_vs_prok2111_as.ffdata
Parsing file #314: processing

Parsing file #381: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_443_vs_prok2111_as.ffdata
Parsing file #382: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_444_vs_prok2111_as.ffdata
Parsing file #383: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_445_vs_prok2111_as.ffdata
Parsing file #384: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_446_vs_prok2111_as.ffdata
Parsing file #385: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_447_vs_prok2111_as.ffdata
Parsing file #386: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_448_vs_prok2111_as.ffdata
Parsing file #387: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_449_vs_prok2111_as.ffdata
Parsing file #388: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_44_vs_prok2111_as.ffdata
Parsing file #389: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_450_vs_prok2111_as.ffdata
Parsing file #390: processing

Parsing file #457: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_511_vs_prok2111_as.ffdata
Parsing file #458: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_512_vs_prok2111_as.ffdata
Parsing file #459: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_513_vs_prok2111_as.ffdata
Parsing file #460: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_514_vs_prok2111_as.ffdata
Parsing file #461: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_515_vs_prok2111_as.ffdata
Parsing file #462: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_516_vs_prok2111_as.ffdata
Parsing file #463: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_517_vs_prok2111_as.ffdata
Parsing file #464: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_518_vs_prok2111_as.ffdata
Parsing file #465: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_519_vs_prok2111_as.ffdata
Parsing file #466: processin

Parsing file #533: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_580_vs_prok2111_as.ffdata
Parsing file #534: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_581_vs_prok2111_as.ffdata
Parsing file #535: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_582_vs_prok2111_as.ffdata
Parsing file #536: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_583_vs_prok2111_as.ffdata
Parsing file #537: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_584_vs_prok2111_as.ffdata
Parsing file #538: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_585_vs_prok2111_as.ffdata
Parsing file #539: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_586_vs_prok2111_as.ffdata
Parsing file #540: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_587_vs_prok2111_as.ffdata
Parsing file #541: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_588_vs_prok2111_as.ffdata
Parsing file #542: processin

Parsing file #609: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_649_vs_prok2111_as.ffdata
Parsing file #610: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_64_vs_prok2111_as.ffdata
Parsing file #611: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_650_vs_prok2111_as.ffdata
Parsing file #612: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_651_vs_prok2111_as.ffdata
Parsing file #613: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_652_vs_prok2111_as.ffdata
Parsing file #614: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_653_vs_prok2111_as.ffdata
Parsing file #615: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_654_vs_prok2111_as.ffdata
Parsing file #616: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_655_vs_prok2111_as.ffdata
Parsing file #617: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_656_vs_prok2111_as.ffdata
Parsing file #618: processing

Parsing file #685: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_717_vs_prok2111_as.ffdata
Parsing file #686: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_718_vs_prok2111_as.ffdata
Parsing file #687: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_719_vs_prok2111_as.ffdata
Parsing file #688: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_71_vs_prok2111_as.ffdata
Parsing file #689: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_720_vs_prok2111_as.ffdata
Parsing file #690: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_721_vs_prok2111_as.ffdata
Parsing file #691: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_722_vs_prok2111_as.ffdata
Parsing file #692: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_723_vs_prok2111_as.ffdata
Parsing file #693: processing/search/euk72_ep_vs_prok2111_as_NEW/hhsuite/euk72_ep_724_vs_prok2111_as.ffdata
Parsing file #694: processing

In [6]:
search_file = 'processing/search/euk72_ep_vs_prok2111_as_NEW/test.tsv'
search_data = pd.read_csv(search_file, sep='\t', index_col=0)

In [7]:
search_data

Target   Prob       E-value       P-value    Score   SS    Cols  Identities  Similarity  Sum_probs  ...  Template-HMM-end  Template_columns  Template_Neff  Pairwise_cov  Query_sequence                                                           Query_consensus                               Matches                      Target_consensus                       Target_sequence                            Confidence
Query                                                                                                                       ...                                                                                                                                                                                                                                                                                                                   
CEO96764.1          CEO96764.1  100.0  0.000000e+00  0.000000e+00  99999.0  0.0  3449.0         100     100.000    99999.0  ...            3449.0            3449.0            1.4      1.000000     FAKESELFHIT                                                               FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT
EP00930P076561  EP00930P076561  100.0  0.000000e+00  0.000000e+00  99999.0  0.0  3506.0         100     100.000    99999.0  ...            3506.0            3506.0            2.7      1.000000     FAKESELFHIT                                                               FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT
EP00820P003146  EP00820P003146  100.0  0.000000e+00  0.000000e+00  99999.0  0.0  3240.0         100     100.000    99999.0  ...            3240.0            3240.0            1.7      1.000000     FAKESELFHIT                                                               FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT
CBN74174.1          CBN74174.1  100.0  0.000000e+00  0.000000e+00  99999.0  0.0  3681.0         100     100.000    99999.0  ...            3681.0            3681.0            2.0      1.000000     FAKESELFHIT                                                               FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT
CBJ49096.1          CBJ49096.1  100.0  0.000000e+00  0.000000e+00  99999.0  0.0  3983.0         100     100.000    99999.0  ...            3983.0            3983.0            1.3      1.000000     FAKESELFHIT                                                               FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT
...                        ...    ...           ...           ...      ...  ...     ...         ...         ...        ...  ...               ...               ...            ...           ...             ...                                                                       ...                                   ...                                   ...                                   ...                                   ...
XP_015645502.1  XP_015645502.1  100.0  0.000000e+00  0.000000e+00  99999.0  0.0    57.0         100     100.000    99999.0  ...              57.0              57.0            3.1      1.000000     FAKESELFHIT                                                               FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT                           FAKESELFHIT
EP00255P001036  EP00255P001036  100.0  0.000000e+00  0.000000e+00  99999.0  0.0    36.0         100     100.0

In [2]:
# format microcosm using cluster.tsv and lca.tsv


import subprocess

# load search data
search_file = 'processing/search/euk72_ep_vs_prok2111_as_NEW/euk72_ep_vs_prok2111_as_cov80_prob80.tsv'
euk_lca_file = 'processing/euk72_ep/euk72_ep.repseq.cascaded_cluster.lca.tsv'
euk_cluster_file = 'processing/euk72_ep/euk72_ep.repseq.cascaded_cluster.tsv'
prok_cluster_file = 'processing/prok2111_as/prok2111_as.repseq.cascaded_cluster.tsv'


microcosm_root = 'processing/new_microcosm_backup'

search_prob = 80
search_cov =  0.8
euk_min_size = 10
euk_min_taxa_scope = 'superkingdom'
prok_targets_min_size = 5


# load all required data
print(f'Loading Search Data')
search_data = pd.read_csv(search_file, sep='\t')

print(f'Prefiltering Search Data')
# prefilter to remove self hits, filter by probability and pairwise coverage
search_data = search_data[(search_data.Query != search_data.Target) &
                          (search_data.Prob > search_prob) &
                          (search_data.Pairwise_cov > search_cov)]



# load euk cluster and lca data
print('Loading Euk lca data')
euk_lca_data = pd.read_csv(euk_lca_file, sep='\t', index_col=0, names = ['acc', 'acc_id', 'lca', 'name'])

print('Loadning Euk cluster data')
euk_cluster_data = pd.read_csv(euk_cluster_file, sep='\t', index_col=0, names = ['cluster_acc', 'acc'])
euk_cluster_sizes = euk_cluster_data.index.value_counts()

# load prok cluster data
print('Loadning Prok cluster data')
prok_cluster_data = pd.read_csv(prok_cluster_file, sep='\t', index_col=0, names = ['cluster_acc', 'acc'])
prok_cluster_sizes = prok_cluster_data.index.value_counts()


# HHsuite profiles do not match mmseqs clusters since profile labels are taken as firs tfasta sequence not cluster representative
print('Remapping HHsuite IDs to MMSeqs')
search_data['Query'] = euk_cluster_data.reset_index().set_index('acc').loc[search_data.Query].cluster_acc.values
search_data['Target'] = prok_cluster_data.reset_index().set_index('acc').loc[search_data.Target].cluster_acc.values
search_data = search_data.set_index('Query')


# create filter list for wide taxonomic coverage for eukaryotes
unique_euk_queries = search_data.index.unique().values

# retrieve clusters with wide taxonomic representation
superkingdom_euk_clusters = euk_lca_data.reset_index().set_index('lca').loc[euk_min_taxa_scope].acc.unique()

# retreive clusters sufficiently large
euk_large_clusters = euk_cluster_sizes[euk_cluster_sizes >= euk_min_size].index.unique().values

# intersect to create a filter set
filtered_euk_queries = list(set(unique_euk_queries).intersection(set(superkingdom_euk_clusters)).intersection(set(euk_large_clusters)))

search_data_filtered = search_data.loc[filtered_euk_queries]
print(f'Found a total of {search_data_filtered.index.unique().shape[0]} valid microcosms')

# prefilter the clsuter databases for faster lookups
euk_cluster_data_filtered = euk_cluster_data.loc[search_data_filtered.index.unique()] 
prok_cluster_data_filtered = prok_cluster_data.loc[search_data_filtered.Target.unique()]

Loading Search Data
Prefiltering Search Data
Loading Euk lca data
Loadning Euk cluster data
Loadning Prok cluster data
Remapping HHsuite IDs to MMSeqs
Found a total of 36673 valid microcosms


In [34]:
# write microcosms to file

write_data = 

offset = 11352
n = 0 + offset
for microcosm, data in write_data.groupby('Query'):
    
    n += 1
    
    # extract sequence accs from cluster data
    euk_seqs = euk_cluster_data_filtered.loc[microcosm].acc.values
    prok_seqs = prok_cluster_data_filtered.loc[data.Target].acc.unique()
    
    # exclude microcosms with few prok hits
    if len(prok_seqs) < prok_targets_min_size: 
        print(f'Excluding {microcosm} with only {len(prok_seqs)} prok seqs')
    
    # write to files 
    else:
        subprocess.run(f'mkdir {microcosm_root}/{microcosm}/'.split())
        with open(f'{microcosm_root}/{microcosm}/{microcosm}.query.acc', 'w') as query_file:
            query_file.write('\n'.join(euk_seqs))
        with open(f'{microcosm_root}/{microcosm}/{microcosm}.target.acc', 'w') as target_file:
            target_file.write('\n'.join(prok_seqs))

        print(f'Wrote microcosm #{n}: {microcosm} with {len(euk_seqs)} euk seqs and {len(prok_seqs)} prok seqs')

Excluding CBJ25717.1 with only 2 prok seqs
Excluding CBJ27666.1 with only 2 prok seqs
Excluding CEL95665.1 with only 3 prok seqs
Excluding CEM01483.1 with only 2 prok seqs
Excluding CEM17510.1 with only 3 prok seqs
Excluding CEM26988.1 with only 4 prok seqs
Excluding CEM35934.1 with only 2 prok seqs
Excluding CEP02783.1 with only 2 prok seqs
Excluding EP00001P032000 with only 3 prok seqs
Excluding EP00001P180004 with only 3 prok seqs
Excluding EP00001P191479 with only 3 prok seqs
Excluding EP00002P000681 with only 2 prok seqs
Excluding EP00002P016524 with only 2 prok seqs
Excluding EP00002P027343 with only 2 prok seqs
Excluding EP00002P028368 with only 3 prok seqs
Excluding EP00003P001555 with only 2 prok seqs
Excluding EP00003P002662 with only 3 prok seqs
Excluding EP00003P004587 with only 2 prok seqs
Excluding EP00003P005282 with only 2 prok seqs
Excluding EP00003P011162 with only 2 prok seqs
Wrote microcosm #11373: EP00003P012908 with 10 euk seqs and 54 prok seqs
Excluding EP00003P0

Excluding EP00036P013719 with only 3 prok seqs
Wrote microcosm #11508: EP00036P017475 with 10 euk seqs and 61 prok seqs
Excluding EP00037P004092 with only 4 prok seqs
Wrote microcosm #11510: EP00037P017354 with 10 euk seqs and 4062 prok seqs
Excluding EP00037P021751 with only 4 prok seqs
Excluding EP00037P031036 with only 4 prok seqs
Excluding EP00038P012329 with only 2 prok seqs
Excluding EP00038P015155 with only 3 prok seqs
Wrote microcosm #11515: EP00038P015228 with 10 euk seqs and 114 prok seqs
Excluding EP00038P015307 with only 2 prok seqs
Wrote microcosm #11517: EP00038P023321 with 10 euk seqs and 1600 prok seqs
Excluding EP00038P027573 with only 2 prok seqs
Excluding EP00038P028030 with only 3 prok seqs
Wrote microcosm #11520: EP00038P030122 with 10 euk seqs and 6 prok seqs
Excluding EP00039P013659 with only 4 prok seqs
Wrote microcosm #11522: EP00039P014272 with 10 euk seqs and 52 prok seqs
Wrote microcosm #11523: EP00039P020501 with 10 euk seqs and 10373 prok seqs
Excluding EP

Excluding EP00060P039029 with only 3 prok seqs
Wrote microcosm #11655: EP00060P040439 with 10 euk seqs and 6 prok seqs
Excluding EP00060P041065 with only 2 prok seqs
Excluding EP00061P001792 with only 3 prok seqs
Excluding EP00061P002993 with only 2 prok seqs
Excluding EP00061P003909 with only 2 prok seqs
Excluding EP00061P014324 with only 3 prok seqs
Wrote microcosm #11661: EP00061P017589 with 10 euk seqs and 217 prok seqs
Excluding EP00061P019096 with only 2 prok seqs
Excluding EP00062P003360 with only 2 prok seqs
Wrote microcosm #11664: EP00062P012666 with 10 euk seqs and 108 prok seqs
Excluding EP00062P027341 with only 4 prok seqs
Wrote microcosm #11666: EP00063P021422 with 10 euk seqs and 31 prok seqs
Excluding EP00063P022840 with only 4 prok seqs
Excluding EP00063P034422 with only 4 prok seqs
Excluding EP00063P040585 with only 4 prok seqs
Excluding EP00063P058982 with only 2 prok seqs
Excluding EP00063P059154 with only 2 prok seqs
Wrote microcosm #11672: EP00063P065035 with 10 eu

Excluding EP00104P018854 with only 4 prok seqs
Wrote microcosm #11804: EP00104P019597 with 10 euk seqs and 336 prok seqs
Wrote microcosm #11805: EP00104P021791 with 10 euk seqs and 126 prok seqs
Excluding EP00104P024868 with only 3 prok seqs
Excluding EP00104P033672 with only 2 prok seqs
Excluding EP00105P007405 with only 2 prok seqs
Excluding EP00105P011450 with only 3 prok seqs
Wrote microcosm #11810: EP00105P019519 with 10 euk seqs and 16 prok seqs
Excluding EP00105P041749 with only 2 prok seqs
Excluding EP00106P011725 with only 2 prok seqs
Excluding EP00106P015110 with only 4 prok seqs
Wrote microcosm #11814: EP00106P017594 with 10 euk seqs and 94 prok seqs
Wrote microcosm #11815: EP00106P021414 with 10 euk seqs and 9 prok seqs
Wrote microcosm #11816: EP00107P004010 with 10 euk seqs and 317 prok seqs
Wrote microcosm #11817: EP00107P008118 with 10 euk seqs and 17 prok seqs
Wrote microcosm #11818: EP00108P005844 with 10 euk seqs and 29 prok seqs
Excluding EP00108P010477 with only 2 p

Wrote microcosm #11952: EP00153P011790 with 10 euk seqs and 154 prok seqs
Wrote microcosm #11953: EP00154P010105 with 10 euk seqs and 1115 prok seqs
Excluding EP00156P000812 with only 3 prok seqs
Excluding EP00158P000644 with only 2 prok seqs
Wrote microcosm #11956: EP00158P004052 with 10 euk seqs and 8 prok seqs
Excluding EP00158P008044 with only 4 prok seqs
Excluding EP00158P010023 with only 2 prok seqs
Excluding EP00160P003506 with only 2 prok seqs
Excluding EP00160P007976 with only 2 prok seqs
Excluding EP00160P008835 with only 2 prok seqs
Excluding EP00160P009357 with only 4 prok seqs
Wrote microcosm #11963: EP00160P010789 with 10 euk seqs and 9 prok seqs
Excluding EP00160P011398 with only 3 prok seqs
Excluding EP00160P011560 with only 2 prok seqs
Excluding EP00160P011581 with only 4 prok seqs
Wrote microcosm #11967: EP00160P012009 with 10 euk seqs and 5 prok seqs
Excluding EP00160P012357 with only 2 prok seqs
Excluding EP00160P012620 with only 2 prok seqs
Wrote microcosm #11970: 

...

Wrote microcosm #34828: XP_007401149.1 with 19 euk seqs and 1275 prok seqs
Wrote microcosm #34829: XP_007401318.1 with 59 euk seqs and 939 prok seqs
Wrote microcosm #34830: XP_007401400.1 with 20 euk seqs and 36 prok seqs
Wrote microcosm #34831: XP_007401937.1 with 53 euk seqs and 1270 prok seqs
Excluding XP_007403171.1 with only 3 prok seqs
Wrote microcosm #34833: XP_007403268.1 with 76 euk seqs and 7677 prok seqs
Wrote microcosm #34834: XP_007707333.1 with 325 euk seqs and 4608 prok seqs
Wrote microcosm #34835: XP_007707928.1 with 688 euk seqs and 66458 prok seqs
Wrote microcosm #34836: XP_007708052.1 with 10 euk seqs and 149 prok seqs
Wrote microcosm #34837: XP_007708346.1 with 301 euk seqs and 1127 prok seqs
Wrote microcosm #34838: XP_007708949.1 with 13 euk seqs and 14076 prok seqs
Wrote microcosm #34839: XP_007708955.1 with 11 euk seqs and 3581 prok seqs
Wrote microcosm #34840: XP_007708986.1 with 96 euk seqs and 3013 prok seqs
Wrote microcosm #34841: XP_007709317.1 with 10 euk s

Wrote microcosm #34941: XP_009041934.1 with 55 euk seqs and 340 prok seqs
Wrote microcosm #34942: XP_009041975.1 with 14 euk seqs and 3093 prok seqs
Wrote microcosm #34943: XP_009042111.1 with 12 euk seqs and 57 prok seqs
Wrote microcosm #34944: XP_009042588.1 with 225 euk seqs and 36 prok seqs
Wrote microcosm #34945: XP_009043023.1 with 12 euk seqs and 12 prok seqs
Wrote microcosm #34946: XP_009043106.1 with 136 euk seqs and 448 prok seqs
Wrote microcosm #34947: XP_009043672.1 with 17 euk seqs and 87 prok seqs
Wrote microcosm #34948: XP_009045389.1 with 22 euk seqs and 640 prok seqs
Wrote microcosm #34949: XP_009048298.1 with 10 euk seqs and 61 prok seqs
Wrote microcosm #34950: XP_009048761.1 with 32 euk seqs and 801 prok seqs
Wrote microcosm #34951: XP_009050284.1 with 24 euk seqs and 48 prok seqs
Wrote microcosm #34952: XP_009051916.1 with 19 euk seqs and 1127 prok seqs
Wrote microcosm #34953: XP_009052070.1 with 49 euk seqs and 132 prok seqs
Wrote microcosm #34954: XP_009057728.1 w

Excluding XP_015639080.2 with only 4 prok seqs
Wrote microcosm #35056: XP_015641140.1 with 72 euk seqs and 2695 prok seqs
Wrote microcosm #35057: XP_015641441.1 with 27 euk seqs and 15 prok seqs
Wrote microcosm #35058: XP_015641626.1 with 30 euk seqs and 58 prok seqs
Wrote microcosm #35059: XP_015646383.1 with 77 euk seqs and 1701 prok seqs
Wrote microcosm #35060: XP_015647733.1 with 35 euk seqs and 1232 prok seqs
Wrote microcosm #35061: XP_015649397.1 with 200 euk seqs and 17484 prok seqs
Wrote microcosm #35062: XP_016855479.1 with 10 euk seqs and 1162 prok seqs
Wrote microcosm #35063: XP_016858028.1 with 63 euk seqs and 462 prok seqs
Wrote microcosm #35064: XP_016859929.1 with 10 euk seqs and 3967 prok seqs
Excluding XP_016864779.1 with only 4 prok seqs
Wrote microcosm #35066: XP_016875505.1 with 37 euk seqs and 120 prok seqs
Wrote microcosm #35067: XP_016883620.1 with 35 euk seqs and 133 prok seqs
Wrote microcosm #35068: XP_017207671.1 with 10 euk seqs and 197 prok seqs
Wrote microc

Excluding XP_025877299.1 with only 3 prok seqs
Wrote microcosm #35169: XP_025878618.1 with 19 euk seqs and 43 prok seqs
Wrote microcosm #35170: XP_025882421.1 with 21 euk seqs and 1347 prok seqs
Wrote microcosm #35171: XP_025982580.1 with 64 euk seqs and 542 prok seqs
Wrote microcosm #35172: XP_025984535.1 with 25 euk seqs and 44 prok seqs
Wrote microcosm #35173: XP_025985001.1 with 25 euk seqs and 150 prok seqs
Wrote microcosm #35174: XP_026378872.1 with 111 euk seqs and 9 prok seqs
Wrote microcosm #35175: XP_026383361.1 with 49 euk seqs and 1164 prok seqs
Wrote microcosm #35176: XP_026383794.1 with 47 euk seqs and 44 prok seqs
Wrote microcosm #35177: XP_026384204.1 with 63 euk seqs and 4486 prok seqs
Wrote microcosm #35178: XP_026384274.1 with 85 euk seqs and 2884 prok seqs
Wrote microcosm #35179: XP_026384752.1 with 76 euk seqs and 845 prok seqs
Wrote microcosm #35180: XP_026389086.1 with 11 euk seqs and 14 prok seqs
Wrote microcosm #35181: XP_026389938.1 with 39 euk seqs and 371 pr

Wrote microcosm #35283: XP_032222791.1 with 29 euk seqs and 920 prok seqs
Excluding XP_032223703.1 with only 4 prok seqs
Wrote microcosm #35285: XP_032223879.1 with 298 euk seqs and 12 prok seqs
Wrote microcosm #35286: XP_032224107.1 with 26 euk seqs and 6401 prok seqs
Wrote microcosm #35287: XP_032224383.1 with 70 euk seqs and 386 prok seqs
Wrote microcosm #35288: XP_032224474.1 with 29 euk seqs and 10884 prok seqs
Wrote microcosm #35289: XP_032224836.1 with 60 euk seqs and 2440 prok seqs
Wrote microcosm #35290: XP_032225072.1 with 38 euk seqs and 489 prok seqs
Wrote microcosm #35291: XP_032225354.1 with 11 euk seqs and 179 prok seqs
Wrote microcosm #35292: XP_032225630.1 with 23 euk seqs and 5 prok seqs
Wrote microcosm #35293: XP_032225687.1 with 180 euk seqs and 12 prok seqs
Wrote microcosm #35294: XP_032227482.1 with 10 euk seqs and 7 prok seqs
Wrote microcosm #35295: XP_032227920.1 with 21 euk seqs and 34581 prok seqs
Wrote microcosm #35296: XP_032228117.1 with 10 euk seqs and 5 p

In [6]:
from core_functions.hhsuite_functions import merge_hhsuite_search_results


merge_hhsuite_search_results(search_root='processing/search/protatlas_vs_euk72_ep/hhsuite/',
    output_basename = 'processing/search/protatlas_vs_euk72_ep/merged_protatlas_vs_euk72_ep',
    write_tsv=True,
    filter_cov=0.5,
    filter_prob=80)


Merging all files from processing/search/protatlas_vs_euk72_ep/hhsuite/ to processing/search/protatlas_vs_euk72_ep/merged_protatlas_vs_euk72_ep
Parsing file #0: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_0_vs_euk72_ep.ffdata
Parsing file #1: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_10_vs_euk72_ep.ffdata
Parsing file #2: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_11_vs_euk72_ep.ffdata
Parsing file #3: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_12_vs_euk72_ep.ffdata
Parsing file #4: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_13_vs_euk72_ep.ffdata
Parsing file #5: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_14_vs_euk72_ep.ffdata
Parsing file #6: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_15_vs_euk72_ep.ffdata
Parsing file #7: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_16_vs_euk72_ep.ffdata
Parsing file #8: processing/search/protatlas_vs_euk72_ep/

Parsing file #80: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_82_vs_euk72_ep.ffdata
Parsing file #81: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_83_vs_euk72_ep.ffdata
Parsing file #82: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_84_vs_euk72_ep.ffdata
Parsing file #83: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_85_vs_euk72_ep.ffdata
Parsing file #84: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_86_vs_euk72_ep.ffdata
Parsing file #85: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_87_vs_euk72_ep.ffdata
Parsing file #86: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_88_vs_euk72_ep.ffdata
Parsing file #87: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_89_vs_euk72_ep.ffdata
Parsing file #88: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_8_vs_euk72_ep.ffdata
Parsing file #89: processing/search/protatlas_vs_euk72_ep/hhsuite/uniprot_seqs_90_vs_euk72_e

In [308]:
# annotate searchresults with localisation data from protein atlas

#load and sanitize data
search = pd.read_csv('processing/search/protatlas_vs_euk72_ep/merged_protatlas_vs_euk72_ep.tsv', sep='\t', index_col=0)
protatlas = pd.read_csv('/data/tobiassonva/data/databases/human_protein_atlas_localisation/merged_subcell_location.tsv', sep='\t',index_col=0)

search = search[search.index != search.Target]
protatlas = protatlas.reset_index().set_index('Uniprot')
protatlas = protatlas[~protatlas.index.duplicated()]
shared_i = list(set(protatlas.index).intersection(search.index))

# intersect indexes
search = search.loc[shared_i]
protatlas = protatlas.loc[shared_i]

#transfer annotation
search[['Biological_process', 'Molecular_function','Subcellular_location']] = protatlas.loc[search.index][['Biological process', 'Molecular function','Subcellular location']].values

# get all keys for cellular locations and then iterate over keys to find members from protatlas sets
all_locs = set(i for item in search['Subcellular_location'].unique() for i in item.split(','))

#print(*all_locs, sep='\n')
for loc in all_locs:
    print(loc)
    search[loc.replace(' ', '_')] = [True if loc in locs.split(',') else False for locs in search['Subcellular_location']]

# swap and rename Target and Query for consistency
search = search.reset_index().rename(columns={'Query':'Target', 'Target':'Query'}).set_index('Query')

# sum number of unique presences over all hits to a microcosm
# completely incomprehensible
nlocs =  pd.Series({i:len(set(loc for locs in data['Subcellular_location'].values for loc in locs.split(','))) 
                    for i, data in search.groupby('Query')}
)

search['Nlocs'] = nlocs.loc[search.index].values

search.to_csv('processing/euk72_ep/euk72_ep.protatlas_annotation.tsv', sep='\t')

Peroxisomes
Nucleoli
Aggresome
Intermediate filaments
Focal adhesion sites
Vesicles
Endoplasmic reticulum
Cytokinetic bridge
Cell Junctions
Mitotic spindle
Mitochondria
Nuclear speckles
Nucleoplasm
Nucleoli fibrillar center
Nuclear bodies
Microtubules
Lysosomes
Cytosol
Midbody
Midbody ring
Endosomes
Rods & Rings
Nuclear membrane
Centriolar satellite
Golgi apparatus
Actin filaments
Lipid droplets
Cytoplasmic bodies
Plasma membrane
Centrosome


In [309]:
search

Target   Prob        E-value        P-value   Score   SS   Cols  Identities  Similarity  Sum_probs  ...  Rods_&_Rings  Nuclear_membrane  Centriolar_satellite  Golgi_apparatus  Actin_filaments  Lipid_droplets  Cytoplasmic_bodies Plasma_membrane Centrosome Nlocs
Query                                                                                                               ...                                                                                                                                                             
EP00484P026414  P42898  100.0  1.000000e-207  2.000000e-212  1578.6  0.0  595.0          66       1.154      591.5  ...         False             False                 False            False            False           False               False           False      False     1
EP00148P005996  P42898  100.0  6.000000e-177  1.000000e-181  1347.3  0.0  577.0          62       1.112      573.6  ...         False             False                 False            False            False           False               False           False      False     1
EP00104P028025  P42898  100.0  2.000000e-153  3.000000e-158  1152.1  0.0  459.0          62       1.129      455.0  ...         False             False                 False            False            False           False               False           False      False     1
EP00922P043682  P42898  100.0  1.000000e-133  2.000000e-138  1008.1  0.0  444.0          59       1.108      431.2  ...         False             False                 False            False            False           False               False           False      False     1
EP01034P003152  P42898  100.0   6.400000e-77   9.100000e-82   579.4  0.0  334.0          45       0.895      318.2  ...         False             False                 False            False            False           False               False           False      False     1
...                ...    ...            ...            ...     ...  ...    ...         ...         ...        ...  ...           ...               ...                   ...              ...              ...             ...                 ...             ...        ...   ...
EP00063P001888  Q9BQJ4   83.2   5.200000e-01   8.800000e-06    41.2  0.0  151.0          21       0.366      107.0  ...         False              True                 False            False            False           False               False           False      False     6
EP00054P038036  Q9BQJ4   82.6   7.600000e-01   9.600000e-06    40.2  0.0  130.0          20       0.326       84.1  ...         False              True                 False            False            False           False               False           False      False     1
EP00052P004134  Q9BQJ4   82.4   5.400000e-01   1.000000e-05    39.6  0.0  155.0          17       0.290      121.9  ...         False              True                 False            False            False           False               False           False      False     6
EP00815P003005  Q9BQJ4   80.9   7.200000e-01   1.200000e-05    40.2  0.0  147.0          24       0.263       95.1  ...         False              True                 False            False            False           False               False           False      False     1
EP01135P002480  Q9BQJ4   80.5   7.400000e-01   1.300000e-05    38.4  0.0  149.0          16       0.244      111.3  ...         False              True                 False            False            False           False               False           False      False     6

[313582 rows x 51 columns]

In [ ]:
# HHsuite profiles do not match mmseqs clusters since profile labels are taken as firs tfasta sequence not cluster representative
print('Remapping HHsuite IDs to MMSeqs')
search_data['Query'] = euk_cluster_data.reset_index().set_index('acc').loc[search_data.Query].cluster_acc.values
search_data['Target'] = prok_cluster_data.reset_index().set_index('acc').loc[search_data.Target].cluster_acc.values
search_data = search_data.set_index('Query')


In [330]:
euk_cluster_file = 'processing/euk72_ep/euk72_ep.repseq.cascaded_cluster.tsv'
print('Loadning Euk cluster data')
euk_cluster_data = pd.read_csv(euk_cluster_file, sep='\t', index_col=0, names = ['cluster_acc', 'acc'])
euk_cluster_sizes = euk_cluster_data.index.value_counts()

Loadning Euk cluster data


In [331]:
search

Target   Prob        E-value        P-value   Score   SS   Cols  Identities  Similarity  Sum_probs  ...  Rods_&_Rings  Nuclear_membrane  Centriolar_satellite  Golgi_apparatus  Actin_filaments  Lipid_droplets  Cytoplasmic_bodies Plasma_membrane Centrosome Nlocs
Query                                                                                                               ...                                                                                                                                                             
EP00484P026414  P42898  100.0  1.000000e-207  2.000000e-212  1578.6  0.0  595.0          66       1.154      591.5  ...         False             False                 False            False            False           False               False           False      False     1
EP00148P005996  P42898  100.0  6.000000e-177  1.000000e-181  1347.3  0.0  577.0          62       1.112      573.6  ...         False             False                 False            False            False           False               False           False      False     1
EP00104P028025  P42898  100.0  2.000000e-153  3.000000e-158  1152.1  0.0  459.0          62       1.129      455.0  ...         False             False                 False            False            False           False               False           False      False     1
EP00922P043682  P42898  100.0  1.000000e-133  2.000000e-138  1008.1  0.0  444.0          59       1.108      431.2  ...         False             False                 False            False            False           False               False           False      False     1
EP01034P003152  P42898  100.0   6.400000e-77   9.100000e-82   579.4  0.0  334.0          45       0.895      318.2  ...         False             False                 False            False            False           False               False           False      False     1
...                ...    ...            ...            ...     ...  ...    ...         ...         ...        ...  ...           ...               ...                   ...              ...              ...             ...                 ...             ...        ...   ...
EP00063P001888  Q9BQJ4   83.2   5.200000e-01   8.800000e-06    41.2  0.0  151.0          21       0.366      107.0  ...         False              True                 False            False            False           False               False           False      False     6
EP00054P038036  Q9BQJ4   82.6   7.600000e-01   9.600000e-06    40.2  0.0  130.0          20       0.326       84.1  ...         False              True                 False            False            False           False               False           False      False     1
EP00052P004134  Q9BQJ4   82.4   5.400000e-01   1.000000e-05    39.6  0.0  155.0          17       0.290      121.9  ...         False              True                 False            False            False           False               False           False      False     6
EP00815P003005  Q9BQJ4   80.9   7.200000e-01   1.200000e-05    40.2  0.0  147.0          24       0.263       95.1  ...         False              True                 False            False            False           False               False           False      False     1
EP01135P002480  Q9BQJ4   80.5   7.400000e-01   1.300000e-05    38.4  0.0  149.0          16       0.244      111.3  ...         False              True                 False            False            False           False               False           False      False     6

[313582 rows x 51 columns]

In [332]:
search.reset_index(inplace=True)

In [334]:
search['Query'] = euk_cluster_data.reset_index().set_index('acc').loc[search.Query].cluster_acc.values

In [337]:
search.set_index('Query').to_csv('processing/euk72_ep/euk72_ep.protatlas_annotation.tsv', sep='\t')

In [328]:
data = next(a)

#set(loc for locs in data[1]['Subcellular_location'].values for loc in locs.split(','))
print(data[0])
locs = data[1].iloc[:,-55:].T
locs
#locs[locs != False]

CBJ29057.1


Query                                                            CBJ29057.1                                        CBJ29057.1       CBJ29057.1
Target                                                               Q9NR31                                            Q9Y6B6           Q9Y5M8
Prob                                                                   97.7                                              97.7             99.7
E-value                                                                 0.0                                               0.0              0.0
P-value                                                                 0.0                                               0.0              0.0
Score                                                                  85.3                                              85.8            171.0
SS                                                                      0.0                                               0.0              0.0
Cols                                                                  180.0                                             180.0            202.0
Identities                                                               26                                                27               32
Similarity                                                            0.321                                              0.32            0.458
Sum_probs                                                             129.4                                             129.1            175.8
Query-HMM-start                                                          18                                                18               58
Query-HMM-end                                                         197.0                                             197.0            270.0
Template-HMM-start                                                      134                                               134              136
Template-HMM-end                                                      348.0                                             348.0            347.0
Template_columns                                                      349.0                                             349.0            349.0
Template_Neff                                                           1.7                                               1.7              1.7
Pairwise_cov                                                       0.515759                                          0.515759         0.610315
Biological_process         ER-Golgi transport, Protein transport, Transport  ER-Golgi transport, Protein transport, Transport              NaN
Molecular_function                                                      NaN                                               NaN         Receptor
Subcellular_location                                  Endoplasmic reticulum                             Endoplasmic reticulum  Plasma membrane
Peroxisomes                                                           False                                             False            False
Nucleoli                                                              False                                             False            False
Aggresome                                                             False                                             False            False
Intermediate_filaments                                                False                                             False            False
Focal_adhesion_sites                                                  False                                             False            False
Vesicles                                                              False                                             False            False
Endoplasmic_reticulum                                                  True                                              True            Fa

In [315]:
search.loc['CBJ25681.1']

Target                                                              Q96F07
Prob                                                                 100.0
E-value                                                                0.0
P-value                                                                0.0
Score                                                                990.8
SS                                                                     0.0
Cols                                                                1211.0
Identities                                                              33
Similarity                                                           0.539
Sum_probs                                                           1099.6
Query-HMM-start                                                         12
Query-HMM-end                                                       1275.0
Template-HMM-start                                                      11
Template-HMM-end         

In [51]:
from core_functions.altair_plots import plot_alignment

aln_file = 'processing/euk72_ep/cluster_fastas/EP00081P018855'

plot, aln_data = plot_alignment(aln_file, seqlimit=100, plot_range=(0,300))
plot

alt.VConcatChart(...)